# Lab Assignment 10: Exploratory Data Analysis, Part 1
## DS 6001: Practice and Application of Data Science
## Name: Afnan Alabdulwahab

### Instructions
Please answer the following questions as completely as possible using text, code, and the results of code as needed. Format your answers in a Jupyter notebook. To receive full credit, make sure you address every part of the problem, and make sure your document is formatted in a clean and professional way.

In this lab, you will be working with the 2018 [General Social Survey (GSS)](http://www.gss.norc.org/). The GSS is a sociological survey created and regularly collected since 1972 by the National Opinion Research Center at the University of Chicago. It is funded by the National Science Foundation. The GSS collects information and keeps a historical record of the concerns, experiences, attitudes, and practices of residents of the United States, and it is one of the most important data sources for the social sciences. 

The data includes features that measure concepts that are notoriously difficult to ask about directly, such as religion, racism, and sexism. The data also include many different metrics of how successful a person is in his or her profession, including income, socioeconomic status, and occupational prestige. These occupational prestige scores are coded separately by the GSS.  The full description of their methodology for measuring prestige is available here: http://gss.norc.org/Documents/reports/methodological-reports/MR122%20Occupational%20Prestige.pdf Here's a quote to give you an idea about how these scores are calculated:

> Respondents then were given small cards which each had a single occupational titles listed on it. Cards were in English or Spanish. They were given one card at a time in the preordained order. The interviewer then asked the respondent to "please put the card in the box at the top of the ladder if you think that occupation has the highest possible social standing. Put it in the box of the bottom of the ladder if you think it has the lowest possible social standing. If it belongs somewhere in between, just put it in the box that matches the social standing of the occupation."

The prestige scores are calculated from the aggregated rankings according to the method described above.

### Problem 0
Import the following packages:

In [43]:
import numpy as np
import pandas as pd
import sidetable
import weighted # this is a module of wquantiles, so type pip install wquantiles or conda install wquantiles to get access to it
import wquantiles
from scipy import stats 
from sklearn import manifold
from sklearn import metrics
import prince
from ydata_profiling import ProfileReport
pd.options.display.max_columns = None

Then load the GSS data with the following code:

In [44]:
%%capture
gss = pd.read_csv("https://github.com/jkropko/DS-6001/raw/master/localdata/gss2018.csv",
                 encoding='cp1252', na_values=['IAP','IAP,DK,NA,uncodeable', 'NOT SURE',
                                               'DK', 'IAP, DK, NA, uncodeable', '.a', "CAN'T CHOOSE"])

### Problem 1
Drop all columns except for the following:
* `id` - a numeric unique ID for each person who responded to the survey
* `wtss` - survey sample weights
* `sex` - male or female
* `educ` - years of formal education
* `region` - region of the country where the respondent lives
* `age` - age
* `coninc` - the respondent's personal annual income
* `prestg10` - the respondent's occupational prestige score, as measured by the GSS using the methodology described above
* `mapres10` - the respondent's mother's occupational prestige score, as measured by the GSS using the methodology described above
* `papres10` -the respondent's father's occupational prestige score, as measured by the GSS using the methodology described above
* `sei10` - an index measuring the respondent's socioeconomic status
* `satjob` - responses to "On the whole, how satisfied are you with the work you do?"
* `fechld` - agree or disagree with: "A working mother can establish just as warm and secure a relationship with her children as a mother who does not work."
* `fefam` - agree or disagree with: "It is much better for everyone involved if the man is the achiever outside the home and the woman takes care of the home and family."
* `fepol` - agree or disagree with: "Most men are better suited emotionally for politics than are most women."
* `fepresch` - agree or disagree with: "A preschool child is likely to suffer if his or her mother works."
* `meovrwrk` - agree or disagree with: "Family life often suffers because men concentrate too much on their work."

Then rename any columns with names that are non-intuitive to you to more intuitive and descriptive ones. Finally, replace the "89 or older" values of `age` with 89, and convert `age` to a float data type. [1 point]

To include only these columns I am defining a list, `gsscolumns`, of these column names, then passing the list to the dataframe index as follows:

In [45]:
gsscolumns = [
    "id",
    "wtss",
    "sex",
    "educ",
    "region",
    "age",
    "coninc",
    "prestg10",
    "mapres10",
    "papres10",
    "sei10",
    "satjob",
    "fechld",
    "fefam",
    "fepol",
    "fepresch",
    "meovrwrk"
]
gss = gss[gsscolumns]
gss

id      wtss     sex  educ       region age       coninc  prestg10  \
0        1  2.357493    male  14.0  new england  43          NaN      47.0   
1        2  0.942997  female  10.0  new england  74   22782.5000      22.0   
2        3  0.942997    male  16.0  new england  42  112160.0000      61.0   
3        4  0.942997  female  16.0  new england  63  158201.8412      59.0   
4        5  0.942997    male  18.0  new england  71  158201.8412      53.0   
...    ...       ...     ...   ...          ...  ..          ...       ...   
2343  2344  0.471499  female  12.0  new england  37          NaN      47.0   
2344  2345  0.942997  female  12.0  new england  75   22782.5000      28.0   
2345  2346  0.942997  female  12.0  new england  67   70100.0000      40.0   
2346  2347  0.942997    male  16.0  new england  72   38555.0000      47.0   
2347  2348  0.471499  female  12.0  new england  79          NaN      33.0   

      mapres10  papres10  sei10          satjob             fechld  \
0         31.0      45.0   65.3  very satisfied     strongly agree   
1         32.0      39.0   14.8             NaN                NaN   
2         32.0      72.0   83.4  mod. satisfied     strongly agree   
3          NaN      39.0   69.3  very satisfied              agree   
4         35.0      45.0   68.6             NaN                NaN   
...        ...       ...    ...             ...                ...   
2343      31.0      72.0   38.8  mod. satisfied           disagree   
2344       NaN      27.0   21.6  very satisfied     strongly agree   
2345      45.0      53.0   41.8             NaN                NaN   
2346      53.0      50.0   62.7             NaN           disagree   
2347       NaN      46.0   13.6  very satisfied  strongly disagree   

                  fefam     fepol           fepresch  \
0              disagree     agree  strongly disagree   
1                   NaN       NaN                NaN   
2              disagree  disagree           disagree   
3              disagree  disagree           disagree   
4                   NaN       NaN                NaN   
...                 ...       ...                ...   
2343  strongly disagree  disagree  strongly disagree   
2344           disagree  disagree           disagree   
2345                NaN       NaN                NaN   
2346              agree  disagree     strongly agree   
2347     strongly agree  disagree     strongly agree   

                        meovrwrk  
0                          agree  
1                            NaN  
2                       disagree  
3     neither agree nor disagree  
4                            NaN  
...                          ...  
2343                    disagree  
2344                    disagree  
2345                         NaN  
2346                       agree  
2347              strongly agree  

[2348 rows x 17 columns]

Using the `.rename()` method on the dataframe, `gss`, with a dictionary parameter that contains mapping of the old column names to the new names, and `axis=1` to work with columns:

In [46]:
gss = gss.rename({"wtss": 'sample_weight',
                  "sex": 'gender',
                  "educ": 'edu_years',
                  "coninc": 'income',
                  "prestg10": 'job_prestige',
                  "mapres10": 'mother_prestige',
                  "papres10": 'father_prestige',
                  "sei10": 'socio_status',
                  "satjob": 'job_satisfaction',
                  "fechld": 'work_mom',
                  "fefam": 'gender_roles',
                  "fepol": 'men_politics',
                  "fepresch": 'preschool_impact',
                  "meovrwrk": 'family_suffers'}, axis=1)
gss

id  sample_weight  gender  edu_years       region age       income  \
0        1       2.357493    male       14.0  new england  43          NaN   
1        2       0.942997  female       10.0  new england  74   22782.5000   
2        3       0.942997    male       16.0  new england  42  112160.0000   
3        4       0.942997  female       16.0  new england  63  158201.8412   
4        5       0.942997    male       18.0  new england  71  158201.8412   
...    ...            ...     ...        ...          ...  ..          ...   
2343  2344       0.471499  female       12.0  new england  37          NaN   
2344  2345       0.942997  female       12.0  new england  75   22782.5000   
2345  2346       0.942997  female       12.0  new england  67   70100.0000   
2346  2347       0.942997    male       16.0  new england  72   38555.0000   
2347  2348       0.471499  female       12.0  new england  79          NaN   

      job_prestige  mother_prestige  father_prestige  socio_status  \
0             47.0             31.0             45.0          65.3   
1             22.0             32.0             39.0          14.8   
2             61.0             32.0             72.0          83.4   
3             59.0              NaN             39.0          69.3   
4             53.0             35.0             45.0          68.6   
...            ...              ...              ...           ...   
2343          47.0             31.0             72.0          38.8   
2344          28.0              NaN             27.0          21.6   
2345          40.0             45.0             53.0          41.8   
2346          47.0             53.0             50.0          62.7   
2347          33.0              NaN             46.0          13.6   

     job_satisfaction           work_mom       gender_roles men_politics  \
0      very satisfied     strongly agree           disagree        agree   
1                 NaN                NaN                NaN          NaN   
2      mod. satisfied     strongly agree           disagree     disagree   
3      very satisfied              agree           disagree     disagree   
4                 NaN                NaN                NaN          NaN   
...               ...                ...                ...          ...   
2343   mod. satisfied           disagree  strongly disagree     disagree   
2344   very satisfied     strongly agree           disagree     disagree   
2345              NaN                NaN                NaN          NaN   
2346              NaN           disagree              agree     disagree   
2347   very satisfied  strongly disagree     strongly agree     disagree   

       preschool_impact              family_suffers  
0     strongly disagree                       agree  
1                   NaN                         NaN  
2              disagree                    disagree  
3              disagree  neither agree nor disagree  
4                   NaN                         NaN  
...                 ...                         ...  
2343  strongly disagree                    disagree  
2344           disagree                    disagree  
2345                NaN                         NaN  
2346     strongly agree                       agree  
2347     strongly agree              strongly agree  

[2348 rows x 17 columns]

Finally, the `replace()` method is used to change occurrences of '89 or older' to '89' in the age column and the `astype()` method is used to convert the age column to a float data type:

In [99]:
gss['age'] = gss['age'].replace('89 or older', '89')
gss['age'] = gss['age'].astype(float)

### Problem 2
#### Part a
Use the `ProfileReport()` function to generate and embed an HTML formatted exploratory data analysis report in your notebook. Make sure that it includes a "Correlations" report along with "Overview" and "Variables". [1 point]

using the `ydata_profiling` library to generate exploratory data analysis report. Initializing the profile report for the `gss` dataset and setting the following parameters:
* `title='2018 General Social Survey (GSS)`: Setting the title of the report.
* `html={'style': {'full_width': True}}`: Configuring the HTML output to use the full width of the display.
* `minimal=False`: Generating a comprehensive report with detailed statistics and visualizations.

In [95]:
profile = ProfileReport(gss,
                       title = '2018 General Social Survey (GSS)',
                       html = {'style': {'full_width':True}},
                       minimal = False)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [100]:
import os
html_file_path = os.path.abspath('gss_profile_report.html')
profile.to_file(html_file_path)
# Display the profile report in the notebook with the full width and a large height
#from IPython.display import IFrame
#IFrame(src='gss_profile_report.html', width='100%', height='12000px')

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

#### Part b
Looking through the HTML report you displayed in part a, how many people in the data are from New England? [1 point]

There are 124 people in the data from New England.

#### Part c
Looking through the HTML report you displayed in part a, which feature in the data has the highest number of missing values, and what percent of the values are missing for this feature? [1 point]

The feature with the highest number of missing values is `men_politics` has 849 (36.2%) missing values. This feature was previously named `fepol` (agree or disagree with: "Most men are better suited emotionally for politics than are most women.").

#### Part d
Looking through the HTML report you displayed in part a, which two distinct features in the data have the highest correlation? [1 point]

From examining the heatmap and the correlation table, the highest correlation is between `job_perstige` and `socio_status` with a correlation coefficinet of 0.824.

### Problem 3
On a primetime show on a 24-hour cable news network, two unpleasant-looking men in suits sit across a table from each other, scowling. One says "This economy is failing the middle-class. The average American today is making less than \\$48,000 a year." The other screams "Fake news! The typical American makes more than \$55,000 a year!" Explain, using words and code, how the data can support both of their arguments. Use the sample weights to calculate descriptive statistics that are more representative of the American adult population as a whole. [1 point]

First, I am creating a new DataFrame `gss_temp` by filtering out rows from the `gss` DataFrame where `income` column is `NaN` (missing values). The `~` operator negates the `isna()` condition, so only rows where `income` is not `NaN` are selected:

In [52]:
gss_temp = gss.loc[~gss.income.isna()]

Next, I am calculating the weighted average of the `income` column from the `gss_temp` DataFrame. I am using the `np.average()` function from the NumPy library to compute the average where the `weights` parameter is set to the `sample_weight` column of `gss_temp`. Each value in `income` is multiplied by its corresponding weight, and the sum of these products is divided by the sum of the weights to produce the weighted average. This process ensures that the average calculation accounts for the sample weights, providing a more accurate representation of the population.

In [53]:
weighted_mean = np.average(gss_temp['income'], weights=gss_temp.sample_weight)
print(f"Weighted Mean Income: ${round(weighted_mean, 2)} a year.")

Weighted Mean Income: $55158.96 a year.


Using the same filtered DataFrame, `gss_temp`, I am calculating the weighted median using `wquantiles.median()`. This function accounts for the sample weights, providing a more accurate representation of the median income for the population.

In [54]:
weighted_median = wquantiles.median(gss_temp.income, gss_temp.sample_weight)
print(f"Weighted Median Income: ${round(weighted_median, 2)} a year.")

Weighted Median Income: $47317.5 a year.


**The Weighted Mean Income** represents the average income, which might be higher due to skewed high incomes.

**The Weighted Median Income** represents the typical income, often lower, reflecting the center of the income distribution.

So both men's statements can be correct. The first man was refering to the **median** income and the second was refereing to the **mean** income.

### Problem 4
For each of the following parts, 
* generate a table that provides evidence about the relationship between the two features in the data that are relevant to each question, 
* interpret the table in words, 
* use a hypothesis test to assess the strength of the evidence in the table, 
* and provide a **specific and accurate** intepretation of the $p$-value associated with this hypothesis test beyond "significant or not". 

#### Part a
Is there a gender wage gap? That is, is there a difference between the average incomes of men and women? [2 points]

This relationship is between a categorical feature (gender) and a continuous feature (income).  The code below groups the dataset by the `gender` column. This means that the data will be split into two groups: one for males and one for females. After grouping, the `agg()` function calculates the mean (average) income for each gender group. The dictionary `{'income':'mean'}` specifies that we want to apply the mean function to the income column. Finally, `.round(2)`, rounds the mean income values to two decimal places for better readability:

In [58]:
gss.groupby('gender').agg({'income':'mean'}).round(2)

income
gender          
female  47191.02
male    53314.63

* On average, women's income is \$47,191.02 per year.
* On average, men's income is \$53,314.63 per year.

Based on the table, this indicates that, on average, men earn more than women. The difference between the average incomes suggests a gender wage gap, with men earning approximately \$6,123.61 more than women annually.

#### Hypothesis Test:
**Null Hypothesis:** Income Mean for Women = Income Mean for Men (no difference in the means) **$H_0: \mu_{women} = \mu_{men}$**

**Alternative Hypothesis:** Income Mean for Women != Income Mean for Men (There is a difference in the means)  **$H_a: \mu_{women} \not = \mu_{men}$**

To test whether we have enough evidence in the data to reject the idea that these means are equal in the population, I will run an independent samples 
t-test in which the null hypothesis is **$H_0: \mu_{women} = \mu_{men}$**.
To run this test, first, I will create two new Python variables, one containing the values of `income` for men, and one containing the values of `income` for women, removing the missing values from both series:

In [59]:
income_men = gss.query("gender=='male'").income.dropna()
income_women = gss.query("gender=='female'").income.dropna()

To perform the t-test and calculate the $p$-value, I will use the `scipy.stats.ttest_ind()` function. The `equal_var=False option` indicates that we do not assume equal population variances:

In [60]:
stats.ttest_ind(income_men, income_women, equal_var=False)

TtestResult(statistic=3.332824087618215, pvalue=0.0008749557881530089, df=2053.1579577339658)

A test statistic of 3.33 means that the observed difference between men's and women's incomes is 3.33 times larger than what would be expected due to random sampling variability if there were no actual difference in the population.

The $p$-value is 0.00087, which is the probability that under the assumption that men and women earn income equally, on average, that we could draw a sample with a difference between these two means of 3.33 or higher. Because this probability is lower than .05, we can reject the null hypothesis and conclude that there is a statisitically significant difference between men and women in terms income.

The test provides strong evidence against the null hypothesis, suggesting that men and women do not earn the same income on average.

#### Part b
Are there different average values of occupational prestige for different levels of job satisfaction? [2 points]

This relationship is between a categorical feature (`job_satisfaction`) and a continuous feature (`job_prestige`). To compare the mean of the values of occupational prestige across the different levels of job satisfaction I will group by the job satisfation levels using `groupby()` on the dataset. This means that the data will be split into groups based on the different levels of job satisfaction (e.g., "very satisfied", "mod. satisfied", "a little dissat", "very dissatisfied"). Then use `.agg()` to get the average values of occupational prestige across the levels. 

In [62]:
gss.groupby('job_satisfaction').agg({'job_prestige':'mean'})

job_prestige
job_satisfaction               
a little dissat       40.946429
mod. satisfied        42.589984
very dissatisfied     43.000000
very satisfied        46.189320

The table shows the average occupational prestige scores for different levels of job satisfaction:

- **Very Satisfied**: Individuals who are very satisfied with their jobs have the highest average job prestige score of approximately 46.19.
- **Moderately Satisfied**: Individuals who are moderately satisfied have an average job prestige score of approximately 42.59.
- **Very Dissatisfied**: Individuals who are very dissatisfied have an average job prestige score of 43.00.
- **A Little Dissatisfied**: Individuals who are a little dissatisfied have the lowest average job prestige score of approximately 40.95.

This suggests that there is a general trend where higher job satisfaction is associated with higher occupational prestige. However, it also highlights that job satisfaction is multi-faceted and influenced by more than just the prestige associated with one's job.

To compare the mean job perstige socores for the different levels of job satisfaction, I will use Analysis of Variance (ANOVA) test. ANOVA helps determine if there are statistically significant differences between the means of three or more groups.

#### Hypothesis Test:
**Null Hypothesis:** The mean job perstige socores for all four different levels of job satisfaction are equal **$H_0: \mu_{1} = \mu_{2} = \mu_{3} = \mu_{4}$**.

**Alternative Hypothesis:** At least one level of job satisfaction mean is different.

To run an ANOVA test in Python, I will use the `stats.f_oneway()` function. I will pass the four series that we want to compare to the function by using `.query()` to select the rows that match each group, dropping missing values for each series. To test whether the different levels of job satisfaction have the same job satisfaction score, on average, I use the following code:

In [63]:
stats.f_oneway(gss.query("job_satisfaction=='a little dissat'").job_prestige.dropna(),
               gss.query("job_satisfaction=='mod. satisfied'").job_prestige.dropna(),
               gss.query("job_satisfaction=='very dissatisfied'").job_prestige.dropna(),
               gss.query("job_satisfaction=='very satisfied'").job_prestige.dropna())

F_onewayResult(statistic=12.205403153509732, pvalue=6.676686425029878e-08)

The $p$-value is 6.676686425029878e-08 (approximately 0.000000066). This means that the probability of observing a difference in job prestige scores as extreme as the one found in our sample, assuming that job satisfaction levels have no effect on job prestige, is incredibly low (about 0.00000668%).

Given this extremely low $p$-value, we reject the null hypothesis, indicating that there is a statistically significant difference in job prestige scores among the different job satisfaction levels. This strong evidence suggests that job satisfaction is indeed related to perceived job prestige.

### Problem 5
Report the Pearson's correlation between years of education, socioeconomic status, income, occupational prestige, and a person's mother's and father's occupational prestige? Then perform a hypothesis test for the correlation between years of education and socioeconomic status and provide a **specific and accurate** intepretation of the $p$-value associated with this hypothesis test beyond "significant or not". [2 points]

To calclate the correlation between the features listed above, I will isolate the corresponding columns of these features from the dataset and apply the `.corr()` method. I will use `.loc` to select all the columns:

In [64]:
gss.loc[:, ['edu_years', 'socio_status', 'income', 'job_prestige', 'mother_prestige', 'father_prestige']].corr()

edu_years  socio_status    income  job_prestige  \
edu_years         1.000000      0.558169  0.389245      0.479933   
socio_status      0.558169      1.000000  0.417210      0.835515   
income            0.389245      0.417210  1.000000      0.340995   
job_prestige      0.479933      0.835515  0.340995      1.000000   
mother_prestige   0.269115      0.203486  0.164881      0.189262   
father_prestige   0.261417      0.210451  0.171048      0.192180   

                 mother_prestige  father_prestige  
edu_years               0.269115         0.261417  
socio_status            0.203486         0.210451  
income                  0.164881         0.171048  
job_prestige            0.189262         0.192180  
mother_prestige         1.000000         0.235750  
father_prestige         0.235750         1.000000

There is a strong positive correlation between job prestige and socioeconomic status (0.8355), indicating that individuals with higher job prestige tend to have higher socioeconomic status.  Years of education are moderately correlated with both socioeconomic status (0.558) and job prestige (0.4799). Income shows moderate correlations with education (0.389), socioeconomic status (0.417), and job prestige (0.340).

#### Hypothesis Test for Correlation Between Years of Education and Socioeconomic Status:
We can use a hypothesis test to confirm that a correlation is not equal to 0, which would let us conclude that two features are correlated to some nonzero extent. Let 
$p$ represent a Pearson’s correlation coefficient. 

**Null Hypothesis:** The Pearson correlation coefficient $p$ between years of education and socioeconomic status is 0. **$H_0: p = 0$**

**Alternative Hypothesis:** The Pearson correlation coefficient $p$ between years of education and socioeconomic status is **NOT** 0. **$H_a: p \not = 0$**

To generate a correlation with an associated $p$-value, we can create a subset of the dataframe that contains only the columns that we want to correlate, remove any row with a missing value from this subset, and pass this subset to the `stats.pearsonr()` function:

In [65]:
gss_corr = gss[['edu_years', 'socio_status']].dropna()
stats.pearsonr(gss_corr['edu_years'], gss_corr['socio_status'])

PearsonRResult(statistic=0.5581686004626785, pvalue=3.7194488100284587e-184)

The Pearson correlation coefficent is 0.558 indicating a moderate to strong positive correlation between years of education and socioeconomic status. As years of education increase, socioeconomic status tends to increase as well. 

The $p$-value $3.72 \times 10^{-184}$  is extremely small indicating that the probability of observing such a correlation by random chance is very low. So, we reject the null hypothesis and coclude that there is a statiscally significant correlation between years of education and socioeconomic status.

### Problem 6
Create a new categorical feature for age groups, with categories for 18-35, 36-49, 50-69, and 70 and older (see the module 8 notebook for an example of how to do this). 

Then create a cross-tabulation in which the rows represent age groups and the columns represent responses to the statement that "It is much better for everyone involved if the man is the achiever outside the home and the woman takes care of the home and family." Rearrange the columns so that they are in the following order: strongly agree, agree, disagree, strongly disagree. Place row percents in the cells of this table.

Finally, use a hypothesis test that can tell use whether there is enough evidence to conclude that these two features have a relationship, and provide a specific and accurate intepretation of the $p$-value. [2 points]

To break the values of the `age` column into categories, I am using `pandas`' `pd.cut()` function. This function create categories from break points in a continuous-valued column. The first argument of the function is the column whose values we want to categorize. I named this column `age`. The second argumnet is `bins` and in it I put a list of the breakpoints (18, 36, 50, 70, 100). The third argument `labels` is a tuple of the labels to assign ('18-35', '36-49', '50-69', '70+').

In [101]:
gss['age_group'] = pd.cut(gss.age, bins=[18, 36, 50, 70, 100], 
                          labels=('18-35', '36-49', '50-69', '70+'))
gss[['age', 'age_group']]

age age_group
0     43.0     36-49
1     74.0       70+
2     42.0     36-49
3     63.0     50-69
4     71.0       70+
...    ...       ...
2343  37.0     36-49
2344  75.0       70+
2345  67.0     50-69
2346  72.0       70+
2347  79.0       70+

[2348 rows x 2 columns]

To reorder categories, I first change the column to a category data type:

In [102]:
gss['gender_roles'] = gss['gender_roles'].astype('category')

Then, I will use the `.cat.reorder_categories()` method to rearrange the columns so that they are in the following order: strongly agree, agree, disagree, strongly disagree:

In [103]:
gss['gender_roles'] = gss['gender_roles'].cat.reorder_categories(['strongly agree', 'agree', 'disagree', 'strongly disagree'])

Lastly, I will use the `pd.crosstab()` function to create a cross-tabulation in which the rows represent age groups and the columns represent responses to the statement that "It is much better for everyone involved if the man is the achiever outside the home and the woman takes care of the home and family.":

To display the row percents instead of counts, I will use th `normalize='index'` argument and multiply the result by 100 to display the percents instead of proportions and round to 2 decimal places:

In [104]:
crosstab = (pd.crosstab(gss.age_group, gss.gender_roles, normalize='index')*100).round(2)
crosstab

gender_roles  strongly agree  agree  disagree  strongly disagree
age_group                                                       
18-35                   3.86  14.73     48.07              33.33
36-49                   5.31  16.48     47.49              30.73
50-69                   4.93  20.49     47.63              26.94
70+                    11.95  34.51     37.61              15.93

Using a hypothesis test that can tell us whether there is enough evidence to conclude that these two features have a relationship:

#### Hypothesis Test:
**Null Hypothesis:** There is no relationship between age groups and responses to the statement about gender roles.

**Alternative Hypothesis:** There is a relationship between age groups and responses to the statement about gender roles.

The hypothesis test that judges the strength of a relationship between two categorical features is $\chi^2$ (chi-square) test of association. To run a $\chi^2$ test, I will pass the `crosstab` variable to the `stats.chi2_contingency()` function:

In [73]:
stats.chi2_contingency(crosstab.values)

Chi2ContingencyResult(statistic=25.71888641227892, pvalue=0.0022708378545913256, dof=9, expected_freq=array([[ 6.51201155, 21.55088352, 45.19660992, 26.73049501],
       [ 6.51331408, 21.55519413, 45.20565014, 26.73584165],
       [ 6.51201155, 21.55088352, 45.19660992, 26.73049501],
       [ 6.51266282, 21.55303883, 45.20113003, 26.73316833]]))

The $p$-value (0.002270) represents the probability that the cross-tab with row-by-row differences as extreme as the ones observed can be generated by a random sample if we assume that age groups and responses to gender roles are independent in the population. In other words, if there were no relationship between age and opinions on gender roles, the row percentages should be constant across rows.

Because the $p$-value is small (less than .05), we reject the null hypothesis and conclude that there is a statistically significant relationship between age groups and opinions on gender roles.

### Problem 7
For this problem, you will conduct and interpret a correspondence analysis on the categorical features that ask respondents to state the extent to which they agree or disagree with the statements:
* `work_mom` - "A working mother can establish just as warm and secure a relationship with her children as a mother who does not work."
* `gender_roles` - "It is much better for everyone involved if the man is the achiever outside the home and the woman takes care of the home and family."
* `men_politics` -  "Most men are better suited emotionally for politics than are most women.
* `preschool_impact` - "A preschool child is likely to suffer if his or her mother works."
* `family_suffers` - "Family life often suffers because men concentrate too much on their work."

#### Part a
Conduct a correspondence analysis using the observed features listed above that measures two latent features. Plot the two latent categories for each category in each of the features used in the analysis. [2 points]

The first step to run MCA is to create a subset of the data that includes only the categorical features we want to use to measure the latent features. And remove rows with missing values:

In [74]:
gss_cat = gss[['work_mom', 'gender_roles', 'men_politics', 'preschool_impact', 'family_suffers']].dropna()
gss_cat

work_mom       gender_roles men_politics   preschool_impact  \
0        strongly agree           disagree        agree  strongly disagree   
2        strongly agree           disagree     disagree           disagree   
3                 agree           disagree     disagree           disagree   
5        strongly agree           disagree     disagree           disagree   
8              disagree  strongly disagree     disagree              agree   
...                 ...                ...          ...                ...   
2341           disagree     strongly agree        agree           disagree   
2343           disagree  strongly disagree     disagree  strongly disagree   
2344     strongly agree           disagree     disagree           disagree   
2346           disagree              agree     disagree     strongly agree   
2347  strongly disagree     strongly agree     disagree     strongly agree   

                  family_suffers  
0                          agree  
2                       disagree  
3     neither agree nor disagree  
5                          agree  
8                          agree  
...                          ...  
2341                       agree  
2343                    disagree  
2344                    disagree  
2346                       agree  
2347              strongly agree  

[1454 rows x 5 columns]

To do a multiple correspondence analysis (MCA), I will use the `prince.MCA()` function from the `prince` package. I specify n_components=2 to generate measures for two latent features, and apply the `.fit()` method to the output, passing the data to this method:

In [75]:
mca = prince.MCA(
     n_components=2
)
mca = mca.fit(gss_cat)

To generate the measurements that are associated with every category, and plot these points. I will use the `.plot()` method from `prince` package:

In [78]:
# the .plot_coordinates() finctions is deprectated in newer versions of prince? so, I'm using plot()
'''ax = mca.plot_coordinates(
    gss_cat,
    ax=None,
    figsize=(12, 12),
    show_row_points=False,
    row_points_size=10,
    show_row_labels=False,
    show_column_points=True,
    column_points_size=30,
    show_column_labels=True,
    legend_n_cols=1
)'''

'ax = mca.plot_coordinates(\n    gss_cat,\n    ax=None,\n    figsize=(12, 12),\n    show_row_points=False,\n    row_points_size=10,\n    show_row_labels=False,\n    show_column_points=True,\n    column_points_size=30,\n    show_column_labels=True,\n    legend_n_cols=1\n)'

In [76]:
mca.plot(
    gss_cat,
    x_component=0,
    y_component=1,
    show_column_markers=True,
    show_row_markers=True,
    show_column_labels=False,
    show_row_labels=False
)

/usr/local/Caskroom/miniconda/base/envs/db_env/lib/python3.12/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/usr/local/Caskroom/miniconda/base/envs/db_env/lib/python3.12/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/usr/local/Caskroom/miniconda/base/envs/db_env/lib/python3.12/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(t

alt.LayerChart(...)

#### Part b
Display the latent features for every category in the observed features, sorted by the first latent feature. Describe in words what concept this feature is attempting to measure, and give the feature a name. [2 points]

In [79]:
mca.column_coordinates(gss_cat).sort_values(1)

0         1
work_mom_agree                             0.080483 -0.586392
gender_roles_disagree                      0.022158 -0.572464
preschool_impact_disagree                 -0.067884 -0.529264
family_suffers_disagree                   -0.228690 -0.242581
family_suffers_agree                       0.358280 -0.187026
family_suffers_neither agree nor disagree -0.480746 -0.163826
gender_roles_agree                         0.878978 -0.076576
men_politics_disagree                     -0.180400 -0.063735
preschool_impact_agree                     0.919993 -0.036434
work_mom_disagree                          0.918045 -0.010327
men_politics_agree                         1.131110  0.399621
work_mom_strongly agree                   -0.901123  0.472181
gender_roles_strongly disagree            -0.922028  0.566797
preschool_impact_strongly disagree        -1.258061  0.886709
family_suffers_strongly disagree          -1.135406  1.283831
family_suffers_strongly agree              0.536784  1.291996
gender_roles_strongly agree                1.564723  2.002688
work_mom_strongly disagree                 1.218716  2.005395
preschool_impact_strongly agree            1.474166  2.233982

* On one end of the spectrum of the first latent feature, we see categories that align with supporting working mothers, rejecting traditional gender roles, and disagreeing with the notion that a preschool child is likely to suffer if his or her mother works (progressive views).
* On the other end, we have categories that align with the belief that men should be the primary achievers outside the home, that preschool children suffer if their mothers work, and not supporting working mothers (traditional views).

A possible feature name can be **Traditional-Progressive Spectrum**.

#### Part c
We can use the results of the MCA model to conduct some cool EDA. For one example, follow these steps:

1. Use the `.row_coordinates()` method to calculate values of the latent feature for every row in the data you passed to the MCA in part a. Extract the first column and store it in its own dataframe.

2. To join it with the full, cleaned GSS data based on row numbers (instead of on a primary key), use the `.join()` method. For example, if we named the cleaned GSS data `gss_clean` and if we named the dataframe in step 1 `latentfeature`, we can type
```
gss_clean = gss_clean.join(latentfeature, how="outer")
```
3. Create a cross-tabuation with age categories (that you constructed in problem 5) in the rows and sex in the columns. Instead of a frequency, place the mean value of the latent feature in the cells. 

What does this table tell you about the relationship between sex, age, and the latent feature? [2 points]

Calculating values of the latent feature for every row. Then, extracting the first column and storing it in it own dataframe:

In [29]:
row_coords = mca.row_coordinates(gss_cat)
latent_feature_df = row_coords.iloc[:, [0]].copy()
latent_feature_df

0
0    -0.202209
2    -0.423361
3    -0.195576
5    -0.240093
8     0.341540
...        ...
2341  1.219018
2343 -0.521776
2344 -0.423361
2346  1.076901
2347  1.440615

[1454 rows x 1 columns]

Giving the column a name before merging:

In [80]:
latent_feature_df.columns = ['latent_feature_1']

In [81]:
gss = gss.join(latent_feature_df, how="outer")

To populate the cells of the cross table with values other than frequency, I am setting the `values` parameter in the `pd.crosstab()` function to `gss.latent_feature_1`. Then, using the `aggfunc` parameter to determine the function to apply within each cell; to report the means, I write `aggfunc='mean'`:

In [83]:
crosstab1 = pd.crosstab(gss.age_group, gss.gender, values=gss.latent_feature_1, aggfunc='mean').round(2)
crosstab1

gender     female  male
age_group              
18-35       -0.22 -0.00
36-49       -0.15  0.01
50-69       -0.13  0.24
70+          0.18  0.48

This cross-tabulation table shows the mean value of the latent feature (which I decided it measures the traditional-progressive spectrum) for different age groups and genders. The younger age groups (18-35 and 36-49) tend to have more progressive views, espacially females. Older age groups (50-69 and 70+) tend to have more traditional view, with males showing stronger traditional views compared to females. The table indicates a clear relationship between age, gender, and the latent feature.